In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import nltk
import re
import os
import string
import spacy
import math
import networkx as nx
import unicodedata
import unidecode
import openai
from openai import OpenAI


from nltk.tokenize import word_tokenize, sent_tokenize
from nltk.corpus import stopwords
from nltk.util import ngrams
from collections import Counter
from wordcloud import WordCloud
from itertools import combinations
from scipy import stats
from collections import defaultdict
from flair.data import Sentence
from flair.models import SequenceTagger
from collections import Counter
from sklearn.feature_extraction.text import TfidfVectorizer
from transformers import pipeline
from textstat import textstat
import hide_code
import ast
import json

from spacy.lang.es.stop_words import STOP_WORDS

In [10]:
GOLD_PATH   = "../datasets/exploration_datasets/gold/"

In [3]:
df = pd.read_excel("../datasets/exploration_datasets/gold/generated_qa_pairs.xlsx")

In [4]:
df.head()

question                answer  \
0  ¿Qué enfermedad padecía Gabriel García Márquez...      cáncer linfático   
1            ¿Dónde falleció Gabriel García Márquez?  en su casa en México   
2  ¿Qué obra maestra publicó García Márquez en 1967?  Cien años de soledad   
3  ¿Quién fue la abuela materna de Gabriel García...   Tranquilina Iguarán   
4  ¿Cuál es el nombre del pueblo ficticio donde s...               Macondo   

   is_impossible                                            context  \
0          False  Se cumplen 10 años desde que Gabo falleció. El...   
1          False  Se cumplen 10 años desde que Gabo falleció. El...   
2          False  Se cumplen 10 años desde que Gabo falleció. El...   
3          False  Se cumplen 10 años desde que Gabo falleció. El...   
4          False  Se cumplen 10 años desde que Gabo falleció. El...   

                                               title category   country  \
0  ¿Qué enfermedad sufrió Gabriel García Márquez ...  cultura  Colombia   
1  ¿Qué enfermedad sufrió Gabriel García Márquez ...  cultura  Colombia   
2  ¿Qué enfermedad sufrió Gabriel García Márquez ...  cultura  Colombia   
3  ¿Qué enfermedad sufrió Gabriel García Márquez ...  cultura  Colombia   
4  ¿Qué enfermedad sufrió Gabriel García Márquez ...  cultura  Colombia   

  newspaper                                           entities  
0    Semana  ['Gabo', 'mundo letras', 'Gabriel García Márqu...  
1    Semana  ['Gabo', 'mundo letras', 'Gabriel García Márqu...  
2    Semana  ['Gabo', 'mundo letras', 'Gabriel García Márqu...  
3    Semana  ['Gabo', 'mundo letras', 'Gabriel García Márqu...  
4    Semana  ['Gabo', 'mundo letras', 'Gabriel García Márqu...

In [5]:
# Clean up missing or stringified boolean values
df["is_impossible"] = df["is_impossible"].astype(bool)

In [6]:
def find_answer_span(context, answer):
    """Find start index of answer in context."""
    if not isinstance(answer, str) or not answer.strip():
        return None, None
    start = context.find(answer)
    if start == -1:
        return None, None
    return start, start + len(answer)

records = []

In [7]:
# Group by title and context (so we don't repeat context)
for (title, context), group in df.groupby(["title", "context"]):
    qas = []
    for i, row in group.iterrows():
        if row["is_impossible"]:
            qas.append({
                "id": f"qa-{i}",
                "question": row["question"],
                "is_impossible": True,
                "answers": []
            })
        else:
            start, end = find_answer_span(context, row["answer"])
            if start is None:
                continue
            qas.append({
                "id": f"qa-{i}",
                "question": row["question"],
                "is_impossible": False,
                "answers": [{"text": row["answer"], "answer_start": start}]
            })

    records.append({
        "title": title,
        "paragraphs": [{
            "context": context,
            "qas": qas
        }]
    })

In [8]:
dataset = {"data": records}

In [9]:
dataset

{'data': [{'title': '"Amo Oaxaca y los encuentros con los lados brillantes y oscuros de su historia y cultura"',
   'paragraphs': [{'context': '. Este espíritu se inclinó por el camino de la luz difundida en el metauniverso sonoro. Tras pasar los primeros años de su adolescencia en la capital de Illinois, se mudó a San Francisco para perfeccionar sus estudios musicales. Ahí conoció a Blaine L. Reininger con quien creó Tuxedomoon, conjunto de experimentadores que en su tiempo fueron considerados como vanguardistas. Dejó Estados Unidos a principios de la década de 1980. Viró a Europa y se estableció en Bruselas (Bélgica) por 12 años. Luego de un viaje a México y tras degustar la naturaleza de nuestro país, pareció recordar su raíz real y decidió no dejarla. Era 1993. Primero estuvo en la Ciudad de México y luego se trasladó a Oaxaca (de donde sabía, sólo era tierra de artistas plásticos), pero la conoció y decidió ser parte de ella. Esteban Café o, Steven Brown es un hombre con la capaci

In [11]:
# Save to JSON
with open(GOLD_PATH  + "qa_dataset_col_mex_news_squad2.json", "w", encoding="utf-8") as f:
    json.dump(dataset, f, ensure_ascii=False, indent=2)

In [15]:
with open(GOLD_PATH  + "qa_dataset_col_mex_news_squad2.json", "r", encoding="utf-8") as f:
    data = json.load(f)

In [12]:
print("✅ SQuAD2-style dataset saved to qa_dataset_squad2.json")

✅ SQuAD2-style dataset saved to qa_dataset_squad2.json


In [16]:
# Pretty-print just the first entry
print(json.dumps(data["data"][0], ensure_ascii=False, indent=2))

{
  "title": "\"Amo Oaxaca y los encuentros con los lados brillantes y oscuros de su historia y cultura\"",
  "paragraphs": [
    {
      "context": ". Este espíritu se inclinó por el camino de la luz difundida en el metauniverso sonoro. Tras pasar los primeros años de su adolescencia en la capital de Illinois, se mudó a San Francisco para perfeccionar sus estudios musicales. Ahí conoció a Blaine L. Reininger con quien creó Tuxedomoon, conjunto de experimentadores que en su tiempo fueron considerados como vanguardistas. Dejó Estados Unidos a principios de la década de 1980. Viró a Europa y se estableció en Bruselas (Bélgica) por 12 años. Luego de un viaje a México y tras degustar la naturaleza de nuestro país, pareció recordar su raíz real y decidió no dejarla. Era 1993. Primero estuvo en la Ciudad de México y luego se trasladó a Oaxaca (de donde sabía, sólo era tierra de artistas plásticos), pero la conoció y decidió ser parte de ella. Esteban Café o, Steven Brown es un hombre con la 